In [86]:
import os
os.environ['USE_PYGEOS'] = '0'
import numpy as np
import pandas as pd
import geopandas as gpd
from pathlib import Path
import rioxarray as rxr
from tqdm.auto import tqdm

In [79]:
from lisfloodreservoirs.utils.utils import filter_domain, filter_reservoirs, find_connections, remove_duplicates

C:\DEV\Anaconda3\envs\xr\lib\site-packages\scipy\__init__.py:146: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.26.4
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"


In [3]:
path = Path('Z:/nahaUsers/casadje/EFASv6')

In [81]:
# load the domain
domain = rxr.open_rasterio(Path('Z:/nahaUsers/casadje/EFASv5') / 'static_maps' / 'domain_area_European_01min.nc').squeeze(dim='band')
lon_min, lat_min, lon_max, lat_max = np.round(domain.rio.bounds(), 6)
efas_cellsize = np.mean(np.diff(domain.x)) # degrees

## Data

### Hylak

In [35]:
hylak_EU = gpd.read_file(path / 'lakes' / 'hydrolakes_domain.shp').set_index('Hylak_id', drop=True)
hylak_EU.Grand_id = hylak.Grand_id.replace(0, np.nan)

In [48]:
hylak_EU.Lake_type.value_counts()

1    101839
2      1415
3        58
Name: Lake_type, dtype: int64

In [47]:
hylak_EU.Grand_id.notnull().sum()

1473

In [46]:
hylak_EU.Grand_id.isnull().sum()

101839

### GRanD

In [ ]:
grand = gpd.read_file('Z:/nahaUsers/casadje/datasets/reservoirs/GRanD/v1_3/GRanD_dams_v1_3.shp').set_index('GRAND_ID')

In [87]:
# keep points inside the domain
pbar = tqdm(grand.iterrows(), total=grand.shape[0])
mask_domain = [
    ID for ID, point in pbar
    if domain.sel(x=point.geometry.x, y=point.geometry.y, method='nearest').item() == 1
]

  0%|          | 0/7320 [00:00<?, ?it/s]

C:\DEV\Anaconda3\envs\xr\lib\site-packages\xarray\core\indexes.py:234: FutureWarning: Passing method to Float64Index.get_loc is deprecated and will raise in a future version. Use index.get_indexer([item], method=...) instead.
  indexer = self.index.get_loc(
C:\DEV\Anaconda3\envs\xr\lib\site-packages\xarray\core\indexes.py:234: FutureWarning: Passing method to Float64Index.get_loc is deprecated and will raise in a future version. Use index.get_indexer([item], method=...) instead.
  indexer = self.index.get_loc(
C:\DEV\Anaconda3\envs\xr\lib\site-packages\xarray\core\indexes.py:234: FutureWarning: Passing method to Float64Index.get_loc is deprecated and will raise in a future version. Use index.get_indexer([item], method=...) instead.
  indexer = self.index.get_loc(
C:\DEV\Anaconda3\envs\xr\lib\site-packages\xarray\core\indexes.py:234: FutureWarning: Passing method to Float64Index.get_loc is deprecated and will raise in a future version. Use index.get_indexer([item], method=...) instead.


In [95]:
grand_EU = grand.loc[mask_domain]

In [97]:
grand.shape, grand_EU.shape

((7320, 58), (1623, 58))

## Lakes

In [26]:
lakes_efas6 = pd.read_excel(path / 'lakes' / 'tables' / 'efas6_lakes.xlsx', index_col='FID')
print(lakes_efas6.GRanD_id.isnull().sum())

219


In [107]:
mask = lakes_efas6.GRanD_id.isnull() & lakes_efas6.Hylak_id.notnull()
hylak.loc[lakes_efas6.loc[mask, 'Hylak_id'].unique(), 'Vol_total'].sum() / hylak.loc[hylak.Grand_id.isnull(), 'Vol_total'].sum()

0.544030513698918

In [108]:
hylak.loc[hylak.Grand_id.isnull(), 'Vol_total'].sum()

3464025.79

In [105]:
lakes_efas6.Hylak_id.isnull().sum() / 

3.4641774419352692e-06

In [17]:
lakes_efas6['volume'] = np.nan

In [23]:
mask

FID
501      True
504      True
505      True
507      True
508      True
        ...  
1299     True
1300     True
1301     True
1302    False
1303     True
Name: Hylak_id, Length: 423, dtype: bool

In [24]:
mask = lakes_efas6.Hylak_id.notnull()
lakes_efas6.loc[mask.index, 'volume'] = hylak.loc[lakes_efas6.loc[mask, 'Hylak_id'], 'Vol_total']

C:\Users\casadje\AppData\Local\Temp\ipykernel_5580\2295545008.py:2: FutureWarning: reindexing with a non-unique Index is deprecated and will raise in a future version.
  lakes_efas6.loc[mask.index, 'volume'] = hylak.loc[lakes_efas6.loc[mask, 'Hylak_id'], 'Vol_total']


ValueError: cannot reindex on an axis with duplicate labels

## Reservoirs

In [53]:
reservoirs_efas6 = pd.concat((
    pd.read_excel(path / 'reservoirs' / 'tables' / 'efas6_reservoirs.xlsx', sheet_name='as_reservoirs', index_col='FID'),
    pd.read_excel(path / 'reservoirs' / 'tables' / 'efas6_reservoirs.xlsx', sheet_name='as_lakes', index_col='FID')
))

reservoirs_efas6.shape

(1545, 25)

In [98]:
reservoirs_efas6.CAP_MCM.sum() /grand_EU.CAP_MCM.sum()

0.8876848136806127